In [2]:
from __future__ import absolute_import

In [1]:
from __future__ import division

In [2]:
from __future__ import print_function

In [3]:
import numpy as np

In [4]:
import tensorflow as tf

d:\anaconda\envs\stable\lib\site-packages\h5py\__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters


In [5]:
tf.logging.set_verbosity(tf.logging.INFO)

In [6]:
def cnn_model_fn(features, labels, mode):
  """Model function for CNN."""
  # Input Layer
  # Reshape X to 4-D tensor: [batch_size, width, height, channels]
  # MNIST images are 28x28 pixels, and have one color channel
  input_layer = tf.reshape(features["x"], [-1, 28, 28, 1])

  # Convolutional Layer #1
  # Computes 32 features using a 5x5 filter with ReLU activation.
  # Padding is added to preserve width and height.
  # Input Tensor Shape: [batch_size, 28, 28, 1]
  # Output Tensor Shape: [batch_size, 28, 28, 32]
  conv1 = tf.layers.conv2d(
      inputs=input_layer,
      filters=32,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)

  # Pooling Layer #1
  # First max pooling layer with a 2x2 filter and stride of 2
  # Input Tensor Shape: [batch_size, 28, 28, 32]
  # Output Tensor Shape: [batch_size, 14, 14, 32]
  pool1 = tf.layers.max_pooling2d(inputs=conv1, pool_size=[2, 2], strides=2)

  # Convolutional Layer #2
  # Computes 64 features using a 5x5 filter.
  # Padding is added to preserve width and height.
  # Input Tensor Shape: [batch_size, 14, 14, 32]
  # Output Tensor Shape: [batch_size, 14, 14, 64]
  conv2 = tf.layers.conv2d(
      inputs=pool1,
      filters=64,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)

  # Pooling Layer #2
  # Second max pooling layer with a 2x2 filter and stride of 2
  # Input Tensor Shape: [batch_size, 14, 14, 64]
  # Output Tensor Shape: [batch_size, 7, 7, 64]
  pool2 = tf.layers.max_pooling2d(inputs=conv2, pool_size=[2, 2], strides=2)

  # Flatten tensor into a batch of vectors
  # Input Tensor Shape: [batch_size, 7, 7, 64]
  # Output Tensor Shape: [batch_size, 7 * 7 * 64]
  pool2_flat = tf.reshape(pool2, [-1, 7 * 7 * 64])

  # Dense Layer
  # Densely connected layer with 1024 neurons
  # Input Tensor Shape: [batch_size, 7 * 7 * 64]
  # Output Tensor Shape: [batch_size, 1024]
  dense = tf.layers.dense(inputs=pool2_flat, units=1024, activation=tf.nn.relu)

  # Add dropout operation; 0.6 probability that element will be kept
  dropout = tf.layers.dropout(
      inputs=dense, rate=0.4, training=mode == tf.estimator.ModeKeys.TRAIN)

  # Logits layer
  # Input Tensor Shape: [batch_size, 1024]
  # Output Tensor Shape: [batch_size, 10]
  logits = tf.layers.dense(inputs=dropout, units=10)

  predictions = {
      # Generate predictions (for PREDICT and EVAL mode)
      "classes": tf.argmax(input=logits, axis=1),
      # Add `softmax_tensor` to the graph. It is used for PREDICT and by the
      # `logging_hook`.
      "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
  }
  if mode == tf.estimator.ModeKeys.PREDICT:
    return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)

  # Calculate Loss (for both TRAIN and EVAL modes)
  loss = tf.losses.sparse_softmax_cross_entropy(labels=labels, logits=logits)

  # Configure the Training Op (for TRAIN mode)
  if mode == tf.estimator.ModeKeys.TRAIN:
    optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
    train_op = optimizer.minimize(
        loss=loss,
        global_step=tf.train.get_global_step())
    return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)

  # Add evaluation metrics (for EVAL mode)
  eval_metric_ops = {
      "accuracy": tf.metrics.accuracy(
          labels=labels, predictions=predictions["classes"])}
  return tf.estimator.EstimatorSpec(
      mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)

In [9]:
def main(unused_argv):
  # Load training and eval data
  mnist = tf.contrib.learn.datasets.load_dataset("mnist")
  train_data = mnist.train.images  # Returns np.array
  train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
  eval_data = mnist.test.images  # Returns np.array
  eval_labels = np.asarray(mnist.test.labels, dtype=np.int32)

  # Create the Estimator
  mnist_classifier = tf.estimator.Estimator(
      model_fn=cnn_model_fn, model_dir="/tmp/mnist_convnet_model1")

  # Set up logging for predictions
  # Log the values in the "Softmax" tensor with label "probabilities"
  tensors_to_log = {"probabilities": "softmax_tensor"}
  logging_hook = tf.train.LoggingTensorHook(
      tensors=tensors_to_log, every_n_iter=50)

  # Train the model
  train_input_fn = tf.estimator.inputs.numpy_input_fn(
      x={"x": train_data},
      y=train_labels,
      batch_size=100,
      num_epochs=None,
      shuffle=True)
  mnist_classifier.train(
      input_fn=train_input_fn,
      steps=20000,
      hooks=[logging_hook])

  # Evaluate the model and print results
  eval_input_fn = tf.estimator.inputs.numpy_input_fn(
      x={"x": eval_data},
      y=eval_labels,
      num_epochs=1,
      shuffle=False)
  eval_results = mnist_classifier.evaluate(input_fn=eval_input_fn)
  print(eval_results)

In [10]:
if __name__ == "__main__":
  tf.app.run()

Extracting MNIST-data\train-images-idx3-ubyte.gz
Extracting MNIST-data\train-labels-idx1-ubyte.gz
Extracting MNIST-data\t10k-images-idx3-ubyte.gz
Extracting MNIST-data\t10k-labels-idx1-ubyte.gz
INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_model_dir': '/tmp/mnist_convnet_model1', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': None, '_save_checkpoints_secs': 600, '_session_config': None, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_service': None, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x00000111F8B7B710>, '_task_type': 'worker', '_task_id': 0, '_global_id_in_cluster': 0, '_master': '', '_evaluation_master': '', '_is_chief': True, '_num_ps_replicas': 0, '_num_worker_replicas': 1}
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Graph was finalized.
INFO:t

INFO:tensorflow:loss = 2.3046458, step = 1
INFO:tensorflow:probabilities = [[0.09496075 0.12515214 0.10054855 0.10063132 0.08657231 0.11787776
  0.09136026 0.09638537 0.08871619 0.09779535]
 [0.09454504 0.11741997 0.10350949 0.10207506 0.08167699 0.08647209
  0.1120515  0.10339103 0.09081141 0.10804734]
 [0.09874149 0.11967491 0.09361334 0.09599385 0.08747195 0.11942986
  0.09309418 0.10619149 0.08642514 0.0993638 ]
 [0.08675795 0.10369422 0.09847569 0.10273688 0.08497544 0.12861972
  0.11170924 0.08741858 0.10594482 0.08966747]
 [0.08821921 0.11262305 0.10102873 0.09722974 0.09340467 0.1034128
  0.10715226 0.10352625 0.09429803 0.09910525]
 [0.08704583 0.10525671 0.10051109 0.10728852 0.09192404 0.08631518
  0.11101228 0.10288236 0.09342861 0.11433534]
 [0.1061554  0.11717366 0.09190948 0.08971061 0.0930127  0.12586445
  0.09621529 0.09093557 0.09185902 0.09716381]
 [0.10120358 0.09925858 0.10010172 0.09777737 0.09286382 0.11355766
  0.10308927 0.0989356  0.09341544 0.09979697]
 [0.09

INFO:tensorflow:global_step/sec: 59.6298
INFO:tensorflow:probabilities = [[0.0994685  0.10349448 0.09478955 0.09726806 0.09205683 0.10393942
  0.09618801 0.10799961 0.10365773 0.10113779]
 [0.10613974 0.10718662 0.09034114 0.11220966 0.09353737 0.11930236
  0.10464856 0.09198193 0.08541615 0.0892365 ]
 [0.09406389 0.11588561 0.09007096 0.10548571 0.08601386 0.11414918
  0.0965873  0.10611675 0.09243798 0.09918864]
 [0.08354951 0.1050309  0.10074974 0.10262853 0.09430129 0.11772684
  0.10378921 0.09274308 0.11282686 0.08665411]
 [0.09974468 0.10568739 0.09267762 0.09973127 0.09597222 0.1101971
  0.09759329 0.09690804 0.09898964 0.1024988 ]
 [0.09731859 0.10240153 0.09893692 0.09700622 0.09768754 0.0993823
  0.09218387 0.10661321 0.10585797 0.10261193]
 [0.09997641 0.10625601 0.10579367 0.10308847 0.07741261 0.10008006
  0.10221796 0.11897834 0.09323184 0.09296469]
 [0.08813993 0.12979448 0.09214727 0.11163792 0.08155209 0.09727459
  0.09550957 0.10167964 0.09867212 0.10359236]
 [0.09427

INFO:tensorflow:loss = 2.2877562, step = 101 (1.684 sec)
INFO:tensorflow:probabilities = [[0.10622676 0.110851   0.08663511 0.11025149 0.09608046 0.11404617
  0.09898008 0.09024642 0.09897876 0.08770375]
 [0.09671108 0.09227426 0.09758022 0.11712431 0.09865688 0.11159877
  0.09125257 0.10565914 0.09333711 0.09580567]
 [0.12381376 0.12111466 0.09843282 0.09889395 0.07358806 0.0958343
  0.08135477 0.09260856 0.11033045 0.10402872]
 [0.10505313 0.0934338  0.10513416 0.09912114 0.07551519 0.11680297
  0.0887028  0.1057856  0.11097731 0.09947392]
 [0.10554998 0.10507347 0.10143023 0.09940676 0.09406    0.09653101
  0.09479933 0.09898569 0.10512947 0.09903418]
 [0.11437195 0.10964978 0.09584863 0.12126829 0.08594351 0.09874515
  0.09944171 0.09048246 0.09113399 0.09311449]
 [0.1007129  0.10674392 0.09426394 0.12564142 0.08179779 0.08564287
  0.10904416 0.09583674 0.09704702 0.10326929]
 [0.09165505 0.11518288 0.0967768  0.09245609 0.08861557 0.12017275
  0.10046187 0.09583618 0.09689279 0.10

INFO:tensorflow:global_step/sec: 66.2003
INFO:tensorflow:probabilities = [[0.10342678 0.10106374 0.08511898 0.09682194 0.09364911 0.09821615
  0.10007522 0.10120673 0.12098657 0.09943479]
 [0.10683289 0.09087618 0.11786272 0.11154289 0.08748793 0.10733125
  0.08989028 0.1051998  0.10001942 0.08295669]
 [0.09905197 0.11387297 0.09318854 0.10053988 0.09512714 0.10426034
  0.09908301 0.09941977 0.09696032 0.09849603]
 [0.10254568 0.10469756 0.10568155 0.10490383 0.09094836 0.10636865
  0.08512278 0.1058915  0.10158964 0.09225053]
 [0.1113262  0.1026749  0.08253777 0.10561068 0.09985868 0.09597105
  0.11052615 0.09245986 0.0976942  0.1013405 ]
 [0.10552102 0.0786758  0.10231189 0.09282842 0.10467286 0.11065324
  0.08700312 0.10549441 0.09418539 0.11865391]
 [0.10220971 0.09826122 0.09287753 0.09379179 0.0946173  0.09762417
  0.11197447 0.098768   0.11061914 0.0992567 ]
 [0.10412825 0.10339627 0.10181697 0.11891247 0.08849873 0.10561861
  0.09330367 0.09062377 0.10760684 0.08609436]
 [0.107

...

INFO:tensorflow:global_step/sec: 54.8875
INFO:tensorflow:probabilities = [[0.00008536 0.00001111 0.00923763 0.00001596 0.01119001 0.00026867
  0.97918415 0.00000002 0.00000695 0.00000012]
 [0.00000614 0.00015223 0.9445612  0.00347178 0.03032821 0.01787867
  0.00239859 0.00078807 0.00018928 0.0002256 ]
 [0.9666008  0.00000077 0.00628788 0.00000371 0.00054862 0.00051763
  0.02431151 0.0015395  0.00003254 0.00015721]
 [0.00566664 0.00031986 0.00708407 0.00446991 0.01038427 0.4097138
  0.02291162 0.00003304 0.43291193 0.10650488]
 [0.1502255  0.00000027 0.04602531 0.00086155 0.00005042 0.00852583
  0.09472027 0.00000745 0.6043056  0.09527775]
 [0.00000003 0.         0.00000004 0.00000435 0.00000018 0.00000021
  0.         0.9999347  0.00000009 0.00006048]
 [0.0000009  0.00001439 0.00272201 0.9968574  0.00000018 0.00002703
  0.00000001 0.00001028 0.00033023 0.00003746]
 [0.00000072 0.00000002 0.00000045 0.00002103 0.00000177 0.00000349
  0.         0.99853504 0.0000007  0.0014367 ]
 [0.0000

INFO:tensorflow:loss = 0.23329803, step = 19901 (1.824 sec)
INFO:tensorflow:probabilities = [[0.00001453 0.96881413 0.00117597 0.00097689 0.00025438 0.0000386
  0.00003312 0.02523598 0.00131034 0.00214598]
 [0.00001858 0.00000045 0.0000379  0.00151601 0.00000836 0.01594969
  0.00000697 0.00000007 0.98220414 0.00025788]
 [0.00021327 0.9745667  0.00069587 0.01355761 0.00161261 0.00205627
  0.00103958 0.00099946 0.00301537 0.00224322]
 [0.0000166  0.00004363 0.00041477 0.00000065 0.00025422 0.00008146
  0.9991861  0.00000003 0.00000207 0.00000057]
 [0.00006712 0.00349934 0.01693018 0.01263353 0.00062853 0.00367781
  0.00284629 0.00605781 0.9022763  0.05138309]
 [0.00000282 0.00000127 0.00094235 0.0000023  0.00014848 0.00031664
  0.9985599  0.00000002 0.00002097 0.0000052 ]
 [0.00000002 0.         0.00000137 0.00015902 0.         0.00000001
  0.         0.999838   0.00000001 0.00000161]
 [0.00002507 0.00002482 0.00025244 0.0000773  0.00000044 0.00001914
  0.00000182 0.00000215 0.99943274 0

INFO:tensorflow:Saving checkpoints for 20000 into /tmp/mnist_convnet_model1\model.ckpt.
INFO:tensorflow:Loss for final step: 0.18915622.
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Starting evaluation at 2018-04-01-03:40:46
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/mnist_convnet_model1\model.ckpt-20000
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Finished evaluation at 2018-04-01-03:40:47
INFO:tensorflow:Saving dict for global step 20000: accuracy = 0.9698, global_step = 20000, loss = 0.10694753
{'accuracy': 0.9698, 'loss': 0.10694753, 'global_step': 20000}


SystemExit: 

d:\anaconda\envs\stable\lib\site-packages\IPython\core\interactiveshell.py:2918: UserWarning: To exit: use 'exit', 'quit', or Ctrl-D.
  warn("To exit: use 'exit', 'quit', or Ctrl-D.", stacklevel=1)
